In [1]:
import os
from kafka import KafkaConsumer
import json
import time
from influxdb_client import InfluxDBClient, Point, WritePrecision
from influxdb_client.client.write_api import SYNCHRONOUS
from datetime import datetime
import numpy as np
import pandas
from tabulate import tabulate

In [2]:
headers=["classification","Normal","Elevated","Hypertension Stage 1","Hypertension Stage 2","Hypertensive Crisis"]
topic_name = "QM_data"
from influxdb_client.client.write_api import SYNCHRONOUS

# InfluxDB connection details
influxdb_host = 'localhost'
influxdb_port = 8086
influxdb_username = 'Rahma'
influxdb_password = 'rahma123'
bucket = "BloodPressure"
organization = "OstProject"
influxdb_token = "NwFT1hvPZogYtaZG4OCUjF0_BJ46riO_DFFXPW6VaHkWQBFcNQdh67nfT6pPuYUH2kWhFDtiY1Cl2BSRAA4VyQ=="

consumer = KafkaConsumer(
    topic_name,
    bootstrap_servers=['localhost:9093'],
    auto_offset_reset='earliest',
    enable_auto_commit=True,
    group_id='python-consumer'
)

#This sketch classifier the coming Diffuse flow values and the count the occurence of each category  
counter={
    "Normal": 0,
    "Elevated": 0,
    "Hypertension Stage 1": 0,
    "Hypertension Stage 2": 0,
    "Hypertensive Crisis": 0
}

# InfluxDB connection details
influxdb_host = 'localhost'
influxdb_port = 8086
influxdb_username = 'Rahma'
influxdb_password = 'rahma123'
bucket = "BloodPressure"
organization = "OstProject"
influxdb_token = "NwFT1hvPZogYtaZG4OCUjF0_BJ46riO_DFFXPW6VaHkWQBFcNQdh67nfT6pPuYUH2kWhFDtiY1Cl2BSRAA4VyQ=="
influx_client = InfluxDBClient(url="http://localhost:8086", token=influxdb_token, org=organization,bucket=bucket)
write_api = influx_client.write_api(write_options=SYNCHRONOUS)
# This sketch classifies the coming Diffuse flow values and counts the occurrence of each category
counter = {
    "Normal": 0,
    "Elevated": 0,
    "Hypertension Stage 1": 0,
    "Hypertension Stage 2": 0,
    "Hypertensive Crisis": 0
}

for message in consumer:
    try:
        mvalue = json.loads(message.value.decode('utf-8'))
        mkey = message.key
        mpart = message.partition
        moffset = message.offset
        print(mvalue)

        # Detect outliers in PowerConsumption_Zone1
        temp1 = float(mvalue['SBP'])
        temp2 = float(mvalue['DBP'])

        print(temp1, temp2)
        if temp1 > 180 or temp2 > 120:
            counter['Hypertensive Crisis'] = counter['Hypertensive Crisis'] + 1
        elif temp1 >= 140 or temp2 >= 90:
            counter['Hypertension Stage 2'] = counter['Hypertension Stage 2'] + 1
        elif temp1 >= 130 or temp2 >= 80:
            counter['Hypertension Stage 1'] = counter['Hypertension Stage 1'] + 1
        elif 120 <= temp1 <= 130 and temp2 < 80:
            counter['Elevated'] = counter['Elevated'] + 1
        elif temp1 < 120 and temp2 < 80:
            counter['Normal'] = counter['Normal'] + 1

        # Write data to InfluxDB
        json_body = [
            {
                "measurement": 'Counter',
                "fields": {
                    "Normal": counter['Normal'],
                    "Elevated": counter['Elevated'],
                    "Hypertension_Stage_1": counter['Hypertension Stage 1'],
                    "Hypertension_Stage_2": counter['Hypertension Stage 2'],
                    "Hypertensive_Crisis": counter['Hypertensive Crisis']
                }
            }
        ]
        data = [['counts', counter['Normal'], counter['Elevated'], counter['Hypertension Stage 1'],
                 counter['Hypertension Stage 2'], counter['Hypertensive Crisis']]]
        print(data)


        write_api.write(bucket, organization, json_body)

        # Print data as a table
        
        print(tabulate(data, headers))
        print("-------------------------------------------------------------")

    except json.JSONDecodeError as e:
        print(f"Error decoding JSON: {e}")
         


{'Timestamp': '2020-10-18 15:24:25', 'RR': '35', 'SPO': '99.9', 'MAP': '0', 'SBP': '0', 'DBP': '0', 'HR': '106.9', 'PP': '0', 'CO': '0'}
0.0 0.0
[['counts', 1, 0, 0, 0, 0]]
classification      Normal    Elevated    Hypertension Stage 1    Hypertension Stage 2    Hypertensive Crisis
----------------  --------  ----------  ----------------------  ----------------------  ---------------------
counts                   1           0                       0                       0                      0
-------------------------------------------------------------
{'Timestamp': '2020-10-18 15:25:25', 'RR': '36.4', 'SPO': '100', 'MAP': '87', 'SBP': '98.9', 'DBP': '63.1', 'HR': '107.3', 'PP': '35.8', 'CO': '3841.34'}
98.9 63.1
[['counts', 2, 0, 0, 0, 0]]
classification      Normal    Elevated    Hypertension Stage 1    Hypertension Stage 2    Hypertensive Crisis
----------------  --------  ----------  ----------------------  ----------------------  ---------------------
counts                 